In [1]:
import lightgbm as lgb

In [7]:
import pandas as pd
df = pd.read_csv('../data/train.csv')
test = pd.read_csv('../data/test.csv')

In [12]:
def preprocess(df: pd.DataFrame) -> pd.DataFrame:
    res = df.copy()
    res["clean_title"] = res["clean_title"].fillna("NaN")
    res["is.clean_title"] = res["clean_title"] == "Yes"
    res["age"] = (2024 - res["model_year"]).map(lambda x: max(x, 1))
    res["milage_per_year"] = res["milage"] / res["age"]
    res["had_accident"] = res["accident"] == "At least 1 accident or damage reported"
    res["avg_price"] =  res.groupby(['brand', 'model'])['price'].transform('mean')
    res["model_year"] = res["model_year"]
    return res

In [5]:
def get_avg_price_from_brand_model(df: pd.DataFrame) -> dict:
    return df.groupby(['brand', 'model'])['avg_price'].mean().to_dict()

def get_avg_price_from_brand(df: pd.DataFrame) -> dict:
    return df.groupby('brand')['avg_price'].mean().to_dict()

In [6]:
avg_price_from_brand_model = get_avg_price_from_brand_model(preprocessed)

avg_price_from_brand = get_avg_price_from_brand(preprocessed)

In [8]:
def retrieve_value(brand: str, model: str, from_brand_model: dict, from_brand: dict) -> float:
    """
    Retrieve a value from `avg_price` dictionary using `brand` and `model` as keys.
    If `model` is not found in the dictionary, use `brand` to retrieve the value.
    If `brand` key is not found, return None.
    """
    if (brand, model) in from_brand_model:
        return from_brand_model[(brand, model)]
    if brand in from_brand:
        return from_brand[brand]

    return None

In [9]:
test['avg_price'] = test.apply(lambda x: retrieve_value(x['brand'], x['model'], avg_price_from_brand_model, avg_price_from_brand), axis=1)

In [14]:
def get_X(df: pd.DataFrame) -> pd.DataFrame:
    return df.copy()[["is.clean_title", "milage_per_year", "had_accident", "avg_price", "model_year"]]

def get_y(df: pd.DataFrame) -> pd.Series:
    """
    Returns the 'price' column from the given DataFrame.

    Parameters:
    - df: pd.DataFrame
        The input DataFrame.

    Returns:
    - pd.Series
        The 'price' column as a pandas Series.
    """
    return df.copy()["price"]

In [15]:
from sklearn.model_selection import train_test_split
preprocessed = preprocess(df)
train, val = train_test_split(preprocessed, test_size = 0.3, random_state = 42)

In [16]:
train_X = get_X(train)
train_y = get_y(train)

In [17]:
val_X = get_X(val)
val_y = get_y(val)

In [19]:
train_data = lgb.Dataset(train_X, label=train_y)
val_data = lgb.Dataset(val_X, label=val_y)

In [43]:
params = {
    'objective': 'regression',
    'metric': 'rmse',
    'num_leaves': 15,
    'learning_rate': 0.01,
    'feature_fraction': 0.7,
    'max_depth': 3,
    'seed': 42,
}

model = lgb.train(params, train_data, valid_sets=[val_data], num_boost_round=1000)

[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.084738 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 549
[LightGBM] [Info] Number of data points in the train set: 131973, number of used features: 5
[LightGBM] [Info] Start training from score 43940.411311
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best ga

In [44]:
import numpy as np
from sklearn.metrics import mean_squared_error
def rmse(y_true, y_pred):
    return np.sqrt(mean_squared_error(y_true, y_pred))

In [45]:
y_pred = model.predict(val_X)
rmse(val_y, y_pred)

np.float64(66050.67039928232)

In [30]:
def preprocess_test(df: pd.DataFrame) -> pd.DataFrame:
    res = df.copy()
    res["clean_title"] = res["clean_title"].fillna("NaN")
    res["is.clean_title"] = res["clean_title"] == "Yes"
    res["age"] = (2024 - res["model_year"]).map(lambda x: max(x, 1))
    res["milage_per_year"] = res["milage"] / res["age"]
    res["had_accident"] = res["accident"] == "At least 1 accident or damage reported"
    res["model_year"] = res["model_year"]
    return res

In [46]:
test = preprocess_test(test)
test_X = get_X(test)
test_data = lgb.Dataset(test_X)

In [47]:
lgb_pred = model.predict(test_X)

In [48]:
test['price'] = lgb_pred

In [49]:
test[["id", "price"]].to_csv("../submission/20240910-light-gbm-best-param.csv", index = False)


---

In [42]:
import time
import mlflow

mlflow.set_tracking_uri('http://127.0.0.1:5000')
mlflow.set_experiment('light-gbm')

learning_rates = [0.01, 0.05, 0.1]
feature_fractions = [0.5, 0.7, 0.9]
num_leaves = [15, 31, 63]
max_depth = [-1, 3, 5, 7]

index = 0
for lr in learning_rates:
    for ff in feature_fractions:
        for nl in num_leaves:
            for md in max_depth:
                with mlflow.start_run(nested=True, run_name=f'[{index}] {time.strftime("%Y%m%d-%H%M%S")}') as run:

                    params = {
                        'objective': 'regression',
                        'metric': 'rmse',
                        'num_leaves': nl,
                        'learning_rate': lr,
                        'feature_fraction': ff,
                        'max_depth': md,
                        'seed': 42,
                    }

                    model = lgb.train(params, train_data, valid_sets=[val_data], num_boost_round=1000)
                    y_pred = model.predict(val_X)

                    mlflow.log_metrics({
                    "val_rmse": np.sqrt(mean_squared_error(val_y, y_pred))})

                    mlflow.log_params(params)

                    mlflow.lightgbm.log_model(model, "model")
                    print(f"lr={lr}, ff={ff}, nl={nl}, md={md}: {rmse(val_y, y_pred)}")
                    index += 1

2024/09/10 21:27:15 INFO mlflow.tracking.fluent: Experiment with name 'light-gbm' does not exist. Creating a new experiment.


[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.011382 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 549
[LightGBM] [Info] Number of data points in the train set: 131973, number of used features: 5
[LightGBM] [Info] Start training from score 43940.411311


2024/09/10 21:27:24 WARNING mlflow.models.model: Model logged without a signature and input example. Please set `input_example` parameter when logging the model to auto infer the model signature.
2024/09/10 21:27:24 INFO mlflow.tracking._tracking_service.client: 🏃 View run 20240910-212715 at: http://127.0.0.1:5000/#/experiments/653144688895529070/runs/40ec85ac56944ebab4b844b234e9f31d.
2024/09/10 21:27:24 INFO mlflow.tracking._tracking_service.client: 🧪 View experiment at: http://127.0.0.1:5000/#/experiments/653144688895529070.


lr=0.01, ff=0.5, nl=15, md=-1: 66098.3980505201
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.009750 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 549
[LightGBM] [Info] Number of data points in the train set: 131973, number of used features: 5
[LightGBM] [Info] Start training from score 43940.411311
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightG

2024/09/10 21:27:30 WARNING mlflow.models.model: Model logged without a signature and input example. Please set `input_example` parameter when logging the model to auto infer the model signature.
2024/09/10 21:27:30 INFO mlflow.tracking._tracking_service.client: 🏃 View run 20240910-212724 at: http://127.0.0.1:5000/#/experiments/653144688895529070/runs/037657242d284970bf089b4639bfa956.
2024/09/10 21:27:30 INFO mlflow.tracking._tracking_service.client: 🧪 View experiment at: http://127.0.0.1:5000/#/experiments/653144688895529070.


...

lr=0.1, ff=0.9, nl=63, md=3: 66450.38718516183
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.002991 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 549
[LightGBM] [Info] Number of data points in the train set: 131973, number of used features: 5
[LightGBM] [Info] Start training from score 43940.411311
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning

2024/09/10 21:41:02 WARNING mlflow.models.model: Model logged without a signature and input example. Please set `input_example` parameter when logging the model to auto infer the model signature.
2024/09/10 21:41:02 INFO mlflow.tracking._tracking_service.client: 🏃 View run 20240910-214053 at: http://127.0.0.1:5000/#/experiments/653144688895529070/runs/f0bb6fe791d7436b96b0e1b51e8ab2ed.
2024/09/10 21:41:02 INFO mlflow.tracking._tracking_service.client: 🧪 View experiment at: http://127.0.0.1:5000/#/experiments/653144688895529070.


lr=0.1, ff=0.9, nl=63, md=5: 67967.68394773966
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.007306 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 549
[LightGBM] [Info] Number of data points in the train set: 131973, number of used features: 5
[LightGBM] [Info] Start training from score 43940.411311
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGB

2024/09/10 21:41:17 WARNING mlflow.models.model: Model logged without a signature and input example. Please set `input_example` parameter when logging the model to auto infer the model signature.
2024/09/10 21:41:17 INFO mlflow.tracking._tracking_service.client: 🏃 View run 20240910-214102 at: http://127.0.0.1:5000/#/experiments/653144688895529070/runs/fffe6d99ffd04c96813e8b9f6c7138cf.
2024/09/10 21:41:17 INFO mlflow.tracking._tracking_service.client: 🧪 View experiment at: http://127.0.0.1:5000/#/experiments/653144688895529070.


lr=0.1, ff=0.9, nl=63, md=7: 69724.37452155656
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.024055 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 549
[LightGBM] [Info] Number of data points in the train set: 131973, number of used features: 5
[LightGBM] [Info] Start training from score 43940.411311
